# Read Multiple CSV Files into one Frame in Python

#### [Link to Source data](https://people.highline.edu/mgirvin/excelisfun.htm)

## **Pandas**

### Via read_csv

In [19]:
import pandas as pd
from pathlib import Path

# create a Path instance and filter for only csv files
files = Path("./Data_files/multiple_csvs/").rglob("*.csv")

# read in all the csv files
all_csvs = [pd.read_csv(file) for file in files]

# lump into one table
all_csvs = pd.concat(all_csvs)

all_csvs

City      Date     Sales  StoreID
0         Tacoma  1/1/2014   $17.30      1522
1         Tacoma  1/1/2014   $15.77      1520
2         Tacoma  1/1/2014  $151.36      1520
3         Tacoma  1/1/2014  $168.47      1522
4         Tacoma  1/1/2014  $150.71      1520
...          ...       ...       ...      ...
223593  Portland  2/3/2015   $41.03      1004
223594  Portland  2/3/2015  $162.54      1005
223595  Portland  2/3/2015   $38.38      1002
223596  Portland  2/3/2015   $96.40      1003
223597  Portland  2/3/2015    $8.38      1005

[880349 rows x 4 columns]

### Via Pyjanitor's read_csvs

The above step can be simplified with [pyjanitor's](https://pyjanitor-devs.github.io/pyjanitor/) [read_csvs](https://pyjanitor-devs.github.io/pyjanitor/api/io/#janitor.io.read_csvs) function:

In [20]:
# pip install pyjanitor
from janitor import read_csvs

files = Path("./Data_files/multiple_csvs/").rglob("*.csv")
df = read_csvs(files)
df

City      Date     Sales  StoreID
0         Tacoma  1/1/2014   $17.30      1522
1         Tacoma  1/1/2014   $15.77      1520
2         Tacoma  1/1/2014  $151.36      1520
3         Tacoma  1/1/2014  $168.47      1522
4         Tacoma  1/1/2014  $150.71      1520
...          ...       ...       ...      ...
880344  Portland  2/3/2015   $41.03      1004
880345  Portland  2/3/2015  $162.54      1005
880346  Portland  2/3/2015   $38.38      1002
880347  Portland  2/3/2015   $96.40      1003
880348  Portland  2/3/2015    $8.38      1005

[880349 rows x 4 columns]

### Via read_csv and the command line

In [21]:
import subprocess
from io import StringIO

data = subprocess.run("awk '(NR==1) || (FNR>1)' ./Data_files/multiple_csvs/*.csv", 
                      shell=True, 
                      capture_output=True,
                      text=True).stdout

df = pd.read_csv(StringIO(data))

df

City        Date     Sales  StoreID
0       Oakland    1/1/2014    $9.83       982
1       Oakland    1/1/2014   $28.18       983
2       Oakland    1/1/2014    $6.83       982
3       Oakland    1/1/2014   $43.90       982
4       Oakland    1/1/2014   $17.16       980
...         ...         ...       ...      ...
880344   Tacoma  12/31/2015   $33.68      1523
880345   Tacoma  12/31/2015  $215.98      1521
880346   Tacoma  12/31/2015  $236.86      1521
880347   Tacoma  12/31/2015   $33.02      1522
880348   Tacoma  12/31/2015   $11.32      1523

[880349 rows x 4 columns]

### Via Pyjanitor's read_commandline

Reading via the command line can be simplified via [pyjanitor's](https://pyjanitor-devs.github.io/pyjanitor/) [read_commandline](https://pyjanitor-devs.github.io/pyjanitor/api/io/#janitor.io.read_commandline) function:

In [22]:
# pip install pyjanitor
from janitor import read_commandline

cmd = "awk '(NR==1) || (FNR>1)' ./Data_files/multiple_csvs/*.csv"
df = read_commandline(cmd)
df

City        Date     Sales  StoreID
0       Oakland    1/1/2014    $9.83       982
1       Oakland    1/1/2014   $28.18       983
2       Oakland    1/1/2014    $6.83       982
3       Oakland    1/1/2014   $43.90       982
4       Oakland    1/1/2014   $17.16       980
...         ...         ...       ...      ...
880344   Tacoma  12/31/2015   $33.68      1523
880345   Tacoma  12/31/2015  $215.98      1521
880346   Tacoma  12/31/2015  $236.86      1521
880347   Tacoma  12/31/2015   $33.02      1522
880348   Tacoma  12/31/2015   $11.32      1523

[880349 rows x 4 columns]

## **datatable**

### Via iread

In [23]:
from datatable import fread, iread, rbind

files = Path("./Data_files/multiple_csvs/").rglob("*.csv")

# iread returns an iterator of all files
all_csvs = iread(tuple(files))

# combine into one table with rbind
all_csvs = rbind(all_csvs)

all_csvs

<Frame#1691dc8d0 880349x4>

### Via fread

In [24]:
files = Path("./Data_files/multiple_csvs/").rglob("*.csv")

all_csvs = [fread(filename) for filename in files]

# combine into one frame
rbind(all_csvs)

<Frame#317288840 880349x4>

### Via fread and the command line

In [25]:
# less verbose than the Pandas option
cmd = "awk '(NR==1) || (FNR>1)' ./Data_files/multiple_csvs/*.csv"
all_csvs = fread(cmd = cmd)
all_csvs

<Frame#12ffeb960 880349x4>

## **Polars**

In [26]:
import polars as pl
files = Path("./Data_files/multiple_csvs/*.csv")
pl.read_csv(files)

shape: (880_349, 4)
┌─────────┬────────────┬──────────┬─────────┐
│ City    ┆ Date       ┆ Sales    ┆ StoreID │
│ ---     ┆ ---        ┆ ---      ┆ ---     │
│ str     ┆ str        ┆ str      ┆ i64     │
╞═════════╪════════════╪══════════╪═════════╡
│ Oakland ┆ 1/1/2014   ┆ $9.83    ┆ 982     │
│ Oakland ┆ 1/1/2014   ┆ $28.18   ┆ 983     │
│ Oakland ┆ 1/1/2014   ┆ $6.83    ┆ 982     │
│ Oakland ┆ 1/1/2014   ┆ $43.90   ┆ 982     │
│ Oakland ┆ 1/1/2014   ┆ $17.16   ┆ 980     │
│ …       ┆ …          ┆ …        ┆ …       │
│ Tacoma  ┆ 12/31/2015 ┆ $33.68   ┆ 1523    │
│ Tacoma  ┆ 12/31/2015 ┆ $215.98  ┆ 1521    │
│ Tacoma  ┆ 12/31/2015 ┆ $236.86  ┆ 1521    │
│ Tacoma  ┆ 12/31/2015 ┆ $33.02   ┆ 1522    │
│ Tacoma  ┆ 12/31/2015 ┆ $11.32   ┆ 1523    │
└─────────┴────────────┴──────────┴─────────┘

## **Resources Used**

datatable - [fread](https://datatable.readthedocs.io/en/latest/api/dt/fread.html)

datatable - [iread](https://datatable.readthedocs.io/en/latest/api/dt/iread.html)

pandas - [read_csv](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.read_csv.html)

polars - [read_csv](https://docs.pola.rs/user-guide/io/multiple/#dealing-with-multiple-files)

python - [subprocess](https://docs.python.org/3/library/subprocess.html)

python - [pathlib](https://docs.python.org/3/library/pathlib.html)

StackOverflow - [read csv files via the command line](https://stackoverflow.com/a/58131427/7175713)

## Comments
<script src="https://utteranc.es/client.js"
        repo="samukweku/data-wrangling-blog"
        issue-term="title"
        theme="github-light"
        crossorigin="anonymous"
        async>
</script>